# 1️⃣ Define la problemática y registra el dataset

## Problema: Ver el estado más reciente de un paciente en el hospital

* **¿Qué?** En una unidad de cuidados intensivos (UCI) de un hospital, los equipos médicos (como monitores de corazón y de oxígeno) están constantemente tomando lecturas de los signos vitales de los pacientes. Esto pasa cada pocos minutos para cada paciente.

* **¿Para Quién?** Para el personal médico y de enfermería. Ellos necesitan tomar decisiones rápidas y, para hacerlo, deben ver el estado *actual* y *más reciente* de un paciente de forma inmediata.

* **¿Por Qué es un Problema?** El hospital acumula una cantidad enorme de datos (cientos de miles de registros) muy rápido. Además, diferentes equipos guardan la hora de la lectura en formatos distintos, creando un registro de "marcas de tiempo" desordenado.

    El problema es que cuando un doctor quiere ver cómo está el Paciente 5, no quiere ver una lista de 500 lecturas antiguas. Necesita ver **solo la última lectura válida** de ese paciente. Un sistema de registro simple no puede encontrar esa "última lectura" de forma rápida y confiable en medio de tantos datos y formatos de hora desordenados.

* **¿Cómo Ayuda el Análisis de Datos?** Necesitamos una base de datos analítica porque es capaz de manejar ese gran volumen de información. Nos permite "limpiar" y "entender" todos los formatos de hora diferentes para ponerlos en orden. Más importante aún, nos deja hacer una consulta inteligente que pueda mirar todos los registros de cada paciente y **mostrar únicamente el más reciente**.

    Así, el personal médico ve exactamente lo que necesita (el estado actual) sin tener que "excavar" en el historial de datos.

## Justificación del Dataset

* **Enlace:** `nasirayub2/human-vital-sign-dataset`
* **Explicación:** El dataset que elegí (Vital Signs) es perfecto para esto. Tiene muchísimas filas (cerca de 200,000) que simulan la gran cantidad de datos de un hospital. Lo más importante es que tiene un identificador de paciente (`patient_id`) y una columna de hora (`Timestamp`) con los formatos desordenados que mencionamos. Usar este dataset nos permite demostrar cómo limpiaríamos esos datos y aplicaríamos la lógica para encontrar la última lectura de cada paciente, resolviendo el problema.

# 2️⃣ Diseña el modelo entidad–relación (ERD)
# Modelo ER

# ![Modelo ER](modelo_ER_vital_sign.jpg)

## Descripción del modelo entidad–relación (ERD)

El modelo representa una base de datos analítica diseñada para almacenar, integrar y analizar **registros de signos vitales de pacientes hospitalizados**, junto con métricas derivadas y una tabla unificada de análisis.

---

### ** 1. measurement_patient**
Esta tabla almacena la **información básica del paciente**.  
Contiene atributos demográficos y físicos que permiten calcular indicadores derivados como el IMC (*Body Mass Index*).

**Campos principales:**
- `patient_id` (PK): identificador único del paciente.  
- `age`: edad del paciente.  
- `gender`: género del paciente.  
- `weight_kg`: peso corporal en kilogramos.  
- `height_m`: altura en metros.  

**Relación:** se conecta con las tablas `vital_measurements` y `derived_metrics` a través de `patient_id`.

---

### ** 2. vital_measurements**
Registra los **signos vitales directos** medidos en los pacientes, provenientes de sensores o dispositivos médicos.  
Estos datos son las mediciones básicas y periódicas del estado del paciente.

**Campos principales:**
- `vital_id` (PK): identificador único del registro de signos vitales.  
- `patient_id` (FK): referencia al paciente.  
- `timestamp`: fecha y hora de la medición.  
- `heart_rate`, `respiratory_rate`, `body_temperature`, `oxygen_saturation`, `systolic_blood_pressure`, `diastolic_blood_pressure`.  

**Relación:** está vinculada con `measurement_patient` por `patient_id`, y con `derived_metrics` y `unified_measurements` por `vital_id`.

---

### ** 3. derived_metrics**
Esta tabla almacena **métricas calculadas o derivadas** a partir de los signos vitales y la información física del paciente.  
Sirve para análisis más avanzados como evaluación del riesgo o detección de anomalías.

**Campos principales:**
- `metric_id` (PK): identificador único de la métrica.  
- `patient_id` (FK): referencia al paciente.  
- `vital_id` (FK): referencia al registro vital del cual se derivan las métricas.  
- `derived_hrv`: variabilidad de la frecuencia cardíaca.  
- `derived_pulse_pressure`: diferencia entre presión sistólica y diastólica.  
- `derived_bmi`: índice de masa corporal.  
- `derived_map`: presión arterial media.  
- `risk_category`: nivel de riesgo calculado (bajo, medio, alto).  

**Relación:** está conectada tanto con `measurement_patient` como con `vital_measurements`.

---

### ** 4. unified_measurements**
Es una **tabla analítica unificada** que integra toda la información relevante del paciente: sus datos demográficos, sus signos vitales y las métricas derivadas.  
Sirve para consultas rápidas y análisis globales sin necesidad de unir múltiples tablas.

**Campos principales:**
- `unified_id` (PK): identificador único del registro unificado.  
- `patient_id`, `vital_id`, `metric_id` (FKs): llaves foráneas que integran las tres fuentes de datos.  
- `timestamp`: fecha de la medición.  
- Variables combinadas: `heart_rate`, `respiratory_rate`, `body_temperature`, `oxygen_saturation`, `systolic_blood_pressure`, `diastolic_blood_pressure`, `age`, `gender`, `weight_kg`, `height_m`, `derived_hrv`, `derived_bmi`, `risk_category`, etc.  

**Relación:** consolida la información de todas las demás tablas, actuando como una **vista o tabla resumen** para análisis clínico.

---

### **🔗 Relaciones generales del modelo**
- Un **paciente** puede tener **muchas mediciones vitales** (`1 a N`).  
- Cada registro de signos vitales puede generar **una o varias métricas derivadas** (`1 a N`).  
- La tabla `unified_measurements` combina y consolida toda la información de las tres tablas anteriores para simplificar el análisis.




# 3️⃣ Crea la base de datos e inserta información

In [0]:
!pip install kagglehub[pandas-datasets]>=0.3.8

Note: you may need to restart the kernel using %restart_python or dbutils.library.restartPython() to use updated packages.


#Importamos libreria

In [0]:
import kagglehub
import pandas as pd
import os
import zipfile

In [0]:
#No lo utilizamos en esta actividad.
%pip install ingestar
%restart_python
from ingestar import Ingestar 

In [0]:
def download_dataset_zip(url = ""):
        print("Descargando dataset desde Kaggle...")
        dataset_path = kagglehub.dataset_download(url)
        print("Ruta al dataset:", dataset_path)
        return dataset_path
    
def extract_zip_files(dataset_path):
        zip_files = [f for f in os.listdir(dataset_path) if f.endswith('.zip')]
        if zip_files:
            zip_file = os.path.join(dataset_path, zip_files[0])
            extract_dir = os.path.join(dataset_path, "extracted")
            os.makedirs(extract_dir, exist_ok=True)
            print(f"Extrayendo {zip_file} en {extract_dir}...")
            with zipfile.ZipFile(zip_file, "r") as z:
                z.extractall(extract_dir)
            return extract_dir
        else:
            # Si no se encuentra un ZIP, se verifica si existen archivos CSV en la ruta
            csv_files = [f for f in os.listdir(dataset_path) if f.endswith('.csv')]
            if csv_files:
                print("No se encontró archivo ZIP pero se detectaron archivos CSV; se asume que el dataset ya se encuentra extraído.")
                return dataset_path
            else:
                raise FileNotFoundError("No se encontró ningún archivo .zip ni archivos .csv en la ruta del dataset")

def create_csv(csv_dir):
        #os.makedirs('src/static/csv', exist_ok=True)
        csv_files = [f for f in os.listdir(csv_dir) if f.endswith('.csv')]
        if not csv_files:
            raise FileNotFoundError("No se encontraron archivos CSV en el directorio extraído")

        for file in csv_files:
            file_path = os.path.join(csv_dir, file)
            print(f"Leyendo {file_path}...")
            try:
                df = pd.read_csv(file_path, encoding="latin1")
            except Exception as e:
                print(f"Error al leer {file}: {e}")
                continue
            print(f"Creando/actualizando ")
        print("cvs creado correctamente en ")
        return df

In [0]:
df = pd.DataFrame()
dataset = download_dataset_zip("nasirayub2/human-vital-sign-dataset") 
csv_dir =extract_zip_files(dataset)
df = create_csv(csv_dir)

Descargando dataset desde Kaggle...


100%|██████████| 14.0M/14.0M [00:00<00:00, 59.6MB/s]

Extracting files...


Ruta al dataset: /home/spark-0e31f325-ede0-4690-bbc6-05/.cache/kagglehub/datasets/nasirayub2/human-vital-sign-dataset/versions/1
No se encontró archivo ZIP pero se detectaron archivos CSV; se asume que el dataset ya se encuentra extraído.
Leyendo /home/spark-0e31f325-ede0-4690-bbc6-05/.cache/kagglehub/datasets/nasirayub2/human-vital-sign-dataset/versions/1/human_vital_signs_dataset_2024.csv...
Creando/actualizando 
cvs creado correctamente en 


In [0]:
df.head(3)

Patient ID  Heart Rate  ...  Derived_MAP Risk Category
0           1          60  ...    98.666667     High Risk
1           2          63  ...    98.000000     High Risk
2           3          63  ...    95.666667      Low Risk

[3 rows x 17 columns]

In [0]:
from pyspark.sql.functions import to_date, col

spark_df = spark.createDataFrame(df)

# Convert 'Timestamp' to date type and cast long columns to int
for field in spark_df.schema.fields:
    if field.name == "Timestamp":
        spark_df = spark_df.withColumn("Timestamp", to_date(col("Timestamp")))
    elif field.dataType.typeName() == "long":
        spark_df = spark_df.withColumn(field.name, col(field.name).cast("int"))

**## **# Eliminar la vista temporal --****

In [0]:
spark.sql(
    "DROP VIEW IF EXISTS tabla_vital_signs"
)

DataFrame[]

**## Crear la tabla**

In [0]:
spark_df.createTempView("tabla_vital_signs")
display(spark_df)

Patient ID Heart Rate Respiratory Rate Timestamp Body Temperature Oxygen Saturation Systolic Blood Pressure Diastolic Blood Pressure Age Gender Weight (kg) Height (m) Derived_HRV Derived_Pulse_Pressure Derived_BMI Derived_MAP Risk Category 1 60 12 2024-07-19 36.861707108012936 95.70204560529264 124 86 37 Female 91.54161781042704 1.6793511495386064 0.1210328574047084 38 32.45903107193736 98.66666666666669 High Risk 2 63 18 2024-07-19 36.51163284237428 96.68941321884792 126 84 77 Male 50.704921363786234 1.992546278864286 0.1170615472064754 42 12.77124626305356 98.0 High Risk 3 63 15 2024-07-19 37.05204858016934 98.50826478317362 131 78 68 Female 90.3167596936639 1.770227684332464 0.0531999581506069 53 28.821069406784925 95.66666666666666 Low Risk 4 99 16 2024-07-19 36.654747504854214 95.01180149205474 118 72 41 Female 96.00618785155216 1.833629095455426 0.0644746768346745 46 28.554610608265143 87.33333333333333 High Risk 5 69 16 2024-07-19 36.97509754422735 98.6237917407539 138 76 25 Female 56.02000582141864 1.8664189298722969 0.1184842214202095 62 16.08143828760833 96.66666666666666 High Risk 6 79 12 2024-07-19 36.884979062580214 95.9871292033958 130 70 22 Male 79.86993283621617 1.9223336907147648 0.103963157437102 60 21.61353304286171 90.0 Low Risk 7 81 17 2024-07-19 37.273639584377314 99.45671576538214 118 84 43 Male 57.84656504041972 1.831483806988997 0.0558846524143972 34 17.245326017670862 95.33333333333331 High Risk 8 96 15 2024-07-19 36.85263343367673 97.1241246758814 135 77 72 Female 71.758971665616 1.6038878729923471 0.0734133726982765 58 27.895117756084 96.33333333333331 High Risk 9 83 12 2024-07-19 36.044191421051224 98.58449733479578 111 84 50 Male 79.29533165339934 1.6727351544521356 0.0985195628027585 27 28.339569682837293 93.0 Low Risk 10 66 15 2024-07-19 36.95717841280944 97.91626727887888 131 77 61 Male 53.923400264374514 1.8963808200748644 0.0813638585935069 54 14.994298811649214 95.0 High Risk 11 84 16 2024-07-19 36.27982119835746 98.19939668167716 119 84 35 Female 71.8911298271864 1.9695663813565147 0.0776289241215214 35 18.532502340797333 95.66666666666669 Low Risk 12 84 12 2024-07-19 36.53178753600392 97.9974013231997 137 83 78 Female 99.3141136407496 1.8223973740783324 0.1016246507107768 54 29.903691869979394 101.0 Low Risk 13 72 16 2024-07-19 37.23706954181399 96.58725178890396 112 76 31 Female 50.86972626145258 1.8839393571802967 0.1493607956329277 36 14.332619207836624 88.0 High Risk 14 61 13 2024-07-19 36.50556429762609 96.53272472086178 112 80 45 Female 82.22939150076127 1.5539019000372916 0.110745102769806 32 34.0549213047176 90.66666666666669 High Risk 15 98 12 2024-07-19 37.2615339220957 98.6748399215955 127 87 89 Female 97.43162012894342 1.900942413448079 0.1376639504254099 40 26.962614528055973 100.33333333333331 High Risk 16 99 14 2024-07-19 36.92458635485272 99.99858724037917 121 74 79 Male 60.62135938618223 1.969247054884459 0.0668200113975811 47 15.632385688334448 89.66666666666667 High Risk 17 83 15 2024-07-19 37.22172639012343 96.0734954555799 113 86 23 Male 75.20994662093743 1.646758280852358 0.0610686398808375 27 27.73419523457724 95.0 Low Risk 18 84 16 2024-07-19 36.152087868461685 97.58444091881788 127 89 62 Female 74.61866727568952 1.6643355955779602 0.1167002996283669 38 26.938020852974397 101.66666666666669 Low Risk 19 77 17 2024-07-19 36.807916083430555 96.24222855728394 137 73 57 Female 58.49955451158789 1.774594087553023 0.0575224578577616 64 18.576098205132183 94.33333333333331 Low Risk 20 97 18 2024-07-19 37.472456841088835 98.0429700547652 129 87 84 Female 77.75672758870672 1.9037199288070972 0.0520866359350588 42 21.455165175711944 101.0 High Risk 21 85 13 2024-07-19 37.16282339629116 98.31401277170345 126 85 55 Male 93.12903403316344 1.7541445447603794 0.0962783961932848 41 30.265952348574817 98.66666666666669 High Risk 22 73 17 2024-07-19 36.18151824261385 99.90200580253884 135 84 48 Female 95.09293702290697 1.991996662783528 0.1138440782863872 51 23.964647657876547 101.0 L

**Renombramos los nombres de las columnas**

In [0]:
rename_map = {
    "Patient ID": "patient_id",
    "Heart Rate": "heart_rate",
    "Respiratory Rate": "respiratory_rate",
    "Body Temperature": "body_temperature",
    "Oxygen Saturation": "oxygen_saturation",
    "Systolic Blood Pressure": "systolic_blood_pressure",
    "Diastolic Blood Pressure": "diastolic_blood_pressure",
    "Age": "age",
    "Gender": "gender",
    "Weight (kg)": "weight_kg",
    "Height (m)": "height_m",
    "Derived_HRV": "derived_hrv",
    "Derived_Pulse_Pressure": "derived_pulse_pressure",
    "Derived_BMI": "derived_bmi",
    "Derived_MAP": "derived_map",
    "Timestamp": "timestamp",
    "Risk Category": "risk_category",
}

In [0]:
for old, new in rename_map.items():
    if old in spark_df.columns:
        spark_df = spark_df.withColumnRenamed(old, new)

In [0]:
spark_df.write.mode("overwrite")\
    .option("overwriteSchema", "true")\
    .saveAsTable("tbl_vital_signs")

# 4️⃣ Evidencia con consultas SQL

In [0]:
%sql
SELECT COUNT(*) FROM tbl_vital_signs;

COUNT(*) 200020

In [0]:
%sql
DESCRIBE tbl_vital_signs


col_name data_type comment patient_id int null heart_rate int null respiratory_rate int null timestamp date null body_temperature double null oxygen_saturation double null systolic_blood_pressure int null diastolic_blood_pressure int null age int null gender string null weight_kg double null height_m double null derived_hrv double null derived_pulse_pressure int null derived_bmi double null derived_map double null risk_category string null

In [0]:
%sql
SELECT * FROM tbl_vital_signs
LIMIT 20;

patient_id heart_rate respiratory_rate timestamp body_temperature oxygen_saturation systolic_blood_pressure diastolic_blood_pressure age gender weight_kg height_m derived_hrv derived_pulse_pressure derived_bmi derived_map risk_category 175018 61 16 2024-03-20 37.019494539016854 97.63419927207366 131 77 85 Female 75.89527661088641 1.8056797200510304 0.1288677791273226 54 23.27733770371798 95.0 Low Risk 175019 79 15 2024-03-20 36.94761272678099 97.25010879482257 114 75 48 Male 86.18462434451314 1.7246289733717446 0.1100164291122248 39 28.97600028537614 88.0 Low Risk 175020 63 16 2024-03-20 37.02982496845897 96.93582649023348 133 86 61 Female 65.0816399294781 1.5871142025079803 0.0939052805089219 47 25.837002769339236 101.66666666666669 Low Risk 175021 95 19 2024-03-20 36.24873289295258 96.75732752419388 127 82 25 Male 71.29647570801586 1.5214242727517049 0.1177015555232018 45 30.801181874409327 97.0 High Risk 175022 76 19 2024-03-20 36.62878116972717 98.52063259022049 120 87 64 Female 76.13125607477234 1.9381282772047443 0.1190879168098607 33 20.26739628756455 98.0 Low Risk 175023 71 15 2024-03-20 37.25611947052519 98.36030428108609 127 80 87 Male 88.2874251374214 1.698215353398083 0.0849674255469039 47 30.61352398884673 95.66666666666669 High Risk 175024 85 19 2024-03-20 36.154446044901626 98.63852953560898 129 88 86 Male 61.02529052858373 1.8769465478912977 0.1328787417136371 41 17.322319552350624 101.66666666666669 High Risk 175025 63 13 2024-03-20 36.38379014440024 95.9704923273363 134 85 50 Male 68.76602179884027 1.5937585906128886 0.0667855783306634 49 27.072528724623552 101.33333333333331 Low Risk 175026 77 18 2024-03-20 37.267476546169654 95.99980813034423 127 81 62 Male 94.86581075843914 1.822539364181764 0.0791065132556189 46 28.559847773120335 96.33333333333331 Low Risk 175027 89 17 2024-03-20 36.06080197748504 95.22740266354084 112 86 75 Male 71.77632123615308 1.7316741712260442 0.1475977547108588 26 23.935849033357403 94.66666666666669 Low Risk 175028 93 12 2024-03-20 37.46977142457466 97.68324308630186 128 88 40 Female 61.385489938170366 1.9113858531121335 0.0896187604370817 40 16.802309950312488 101.33333333333331 High Risk 175029 63 19 2024-03-20 37.47033724065065 99.22089545255491 132 83 39 Male 72.1973752008598 1.6920030356659304 0.1254835952935282 49 25.21849313791247 99.33333333333331 Low Risk 175030 85 17 2024-03-20 36.076831169809566 96.12721014261872 128 83 80 Female 92.54520847294448 1.9760183545871897 0.0706036653393502 45 23.70129029033583 98.0 Low Risk 175031 89 17 2024-03-20 36.700076902193466 97.32697150818996 131 77 23 Female 65.09358393891455 1.9573191149688045 0.097919960423872 54 16.99084229560691 95.0 High Risk 175032 85 13 2024-03-20 36.30958399498238 98.746028482092 122 73 51 Male 62.50805806650607 1.6422326176354989 0.1186029575724404 49 23.1775037197726 89.33333333333333 Low Risk 175033 61 13 2024-03-20 36.31038339997116 98.30115776444924 116 87 39 Male 76.5075844459899 1.663883498873958 0.1382574936845965 29 27.63494857721563 96.66666666666669 Low Risk 175034 94 19 2024-03-20 36.109123985460975 95.635505324785 130 71 53 Male 67.15293321397263 1.9202491712391587 0.0942716855538489 59 18.211671776246316 90.66666666666666 High Risk 175035 87 19 2024-03-20 37.152344357606225 95.64546274609812 113 70 87 Female 79.64704626973477 1.5695959762682783 0.1104247153262377 43 32.32912281780815 84.33333333333333 High Risk 175036 62 16 2024-03-20 37.270501532735274 98.77242837838295 117 88 66 Female 97.47042726634996 1.661391980657684 0.0851000653875499 29 35.31251503941223 97.66666666666669 High Risk 175037 81 14 2024-03-20 37.44527588722019 97.47483155246093 139 84 69 Female 78.07079312060824 1.562836113029048 0.1099284759644803 55 31.96404366275255 102.33333333333331 High Risk

In [0]:
%sql
SELECT 
  patient_id,
  gender,
  age,
  timestamp,
  heart_rate,
  body_temperature,
  systolic_blood_pressure,
  diastolic_blood_pressure,
  risk_category
FROM
  tbl_vital_signs
WHERE
  date_format(timestamp, 'yyyy-MM-dd') = '2024-07-19'
  AND risk_category = 'High Risk'
  AND gender = 'Female'
  AND age BETWEEN 40 AND 60
ORDER BY
  heart_rate DESC,
  body_temperature DESC
LIMIT 50;

patient_id gender age timestamp heart_rate body_temperature systolic_blood_pressure diastolic_blood_pressure risk_category 1200 Female 58 2024-07-19 99 37.352948925206725 112 81 High Risk 940 Female 48 2024-07-19 99 36.72460204465527 135 75 High Risk 4 Female 41 2024-07-19 99 36.654747504854214 118 72 High Risk 334 Female 42 2024-07-19 99 36.494935039562634 127 71 High Risk 1195 Female 45 2024-07-19 99 36.20716090525957 132 88 High Risk 1088 Female 40 2024-07-19 99 36.08286009655074 121 71 High Risk 706 Female 59 2024-07-19 99 36.0070159849135 122 70 High Risk 1032 Female 45 2024-07-19 98 37.17452324077412 113 73 High Risk 830 Female 60 2024-07-19 98 36.3988422439448 129 88 High Risk 802 Female 57 2024-07-19 97 37.16132951138101 113 86 High Risk 1087 Female 54 2024-07-19 97 36.713340366263715 119 73 High Risk 245 Female 44 2024-07-19 97 36.64171127009168 134 84 High Risk 360 Female 41 2024-07-19 97 36.167524185768066 113 83 High Risk 93 Female 59 2024-07-19 96 37.30679501450013 116 81 High Risk 77 Female 42 2024-07-19 96 37.10196387110892 111 77 High Risk 1059 Female 56 2024-07-19 96 37.057688010142336 132 84 High Risk 273 Female 46 2024-07-19 96 36.84854933077052 114 78 High Risk 370 Female 47 2024-07-19 96 36.789139465458135 118 81 High Risk 689 Female 52 2024-07-19 96 36.6304458832432 125 83 High Risk 396 Female 50 2024-07-19 96 36.41303151096032 135 84 High Risk 61 Female 52 2024-07-19 95 36.63303504742271 112 78 High Risk 81 Female 56 2024-07-19 95 36.550568181513995 113 78 High Risk 111 Female 57 2024-07-19 95 36.241538497921816 116 72 High Risk 318 Female 56 2024-07-19 95 36.16448247878912 138 70 High Risk 794 Female 58 2024-07-19 95 36.13551936640457 129 78 High Risk 223 Female 46 2024-07-19 94 37.14855807100988 135 80 High Risk 215 Female 42 2024-07-19 94 36.45167652518837 116 84 High Risk 1211 Female 56 2024-07-19 94 36.24029775867814 138 82 High Risk 873 Female 57 2024-07-19 93 37.422126867345696 136 83 High Risk 501 Female 59 2024-07-19 93 37.23468762560002 135 87 High Risk 738 Female 41 2024-07-19 93 36.47342527929023 113 82 High Risk 293 Female 43 2024-07-19 92 37.45183198557 122 83 High Risk 1244 Female 42 2024-07-19 92 37.36606054855661 118 81 High Risk 767 Female 60 2024-07-19 92 37.31916060503757 111 87 High Risk 281 Female 43 2024-07-19 92 37.25871881193058 113 82 High Risk 38 Female 52 2024-07-19 92 37.12879298615971 134 87 High Risk 41 Female 55 2024-07-19 92 36.2059926861605 113 80 High Risk 1284 Female 44 2024-07-19 92 36.06030940857254 130 72 High Risk 535 Female 48 2024-07-19 91 37.4916467756081 117 84 High Risk 89 Female 55 2024-07-19 91 37.474705116257965 122 87 High Risk 999 Female 51 2024-07-19 91 37.28412363721896 131 73 High Risk 42 Female 42 2024-07-19 91 36.32751288842679 111 88 High Risk 961 Female 58 2024-07-19 91 36.201868722098176 119 79 High Risk 704 Female 40 2024-07-19 89 37.10230351024417 130 84 High Risk 910 Female 56 2024-07-19 89 36.59620883897343 119 73 High Risk 1126 Female 42 2024-07-19 89 36.36295992356533 129 75 High Risk 722 Female 49 2024-07-19 89 36.25356019147824 112 84 High Risk 259 Female 50 2024-07-19 88 37.113046046178574 135 72 High Risk 1262 Female 54 2024-07-19 88 36.45564810502329 139 86 High Risk 1023 Female 59 2024-07-19 87 37.41071113242363 124 82 High Risk